In [5]:
# Callback duration
#
# Get trace data using the provided launch file:
#    $ ros2 launch tracetools_analysis pingpong.launch.py
#    (wait a few seconds, then kill with Ctrl+C)
#
# (optional) convert trace data:
#    $ ros2 run tracetools_analysis convert ~/.ros/tracing/pingpong/ust
#
# OR
#
# Use the provided sample converted trace file, changing the path below to:
#    'sample_data/converted_pingpong'

In [3]:
path = '~/.ros/tracing/session-20220527110659/ust'
trace_path = '~/.ros/tracing/session-20220527110659'
#path = 'sample_data/converted_pingpong'

In [4]:
import sys
# Assuming a workspace with:
#   src/tracetools_analysis/
#   src/ros-tracing/ros2_tracing/tracetools_read/
sys.path.insert(0, '../')
sys.path.insert(0, '/opt/autoware_perf/ros2_tracing/tracetools_read/')
import datetime as dt

from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.io import show
from bokeh.layouts import row
from bokeh.models import ColumnDataSource
from bokeh.models import DatetimeTickFormatter
from bokeh.models import PrintfTickFormatter
import numpy as np
import pandas as pd

from tracetools_analysis.loading import load_file
from tracetools_analysis.processor.ros2 import Ros2Handler
from tracetools_analysis.utils.ros2 import Ros2DataModelUtil
from tracetools_analysis.ros_model import ApplicationFactory


In [5]:
# Process
events = load_file(path)
handler = Ros2Handler.process(events)
#handler.data.print_data()

found converted file: /home/usrg/.ros/tracing/session-20220527110659/ust/converted
 [100%] [Ros2Handler]
warn: callback 36010656 is not registered. your application may contain rclpy app.


In [6]:
data_util = Ros2DataModelUtil(handler.data)

callback_symbols = data_util.get_callback_symbols()

output_notebook()
psize = 1080
colours = ['#29788E', '#DD4968', '#410967']

Loading BokehJS ...

In [19]:
from tracetools_analysis.ros_model import ApplicationFactory
from tracetools_analysis.ros_model.application import Application
from tracetools_analysis.ros_model.callback import SubscribeCallback, TimerCallback, Callback
from tracetools_analysis.ros_model.publish import Publish
from tracetools_analysis.ros_model.node import Node
from tracetools_analysis.ros_model.util import Util

def create_node(node_info, data_util):
    if True:
        timer_df = data_util.get_timer_info()
        sub_df = data_util.get_subscribe_info()
        pub_df = data_util.get_publish_info()

        ns, name = Util.to_ns_and_name(node_info['name'])
        node = Node(ns=ns, name=name)

        timer_df_ = timer_df[timer_df['name'] == node.name]
        assert ApplicationFactory._get_duplicate_num_max(timer_df_['period'].values) <= 1,\
            '{} node has same period'.format(node.name)
        for i, (_, df) in enumerate(timer_df_.iterrows()):
            callback = TimerCallback(node=node, period=df['period'], symbol=df['symbol'])
            node.callbacks.append(callback)

        # nif TRACE HACK
        sub_df_ = sub_df[(sub_df['name'] == node.name)]

        # Append 'callback_object' to duplicated topic names (to pass assertions)
        sub_df_.loc[sub_df_.duplicated(keep='first', subset=['topic_name']), 'topic_name'] = \
            sub_df_.loc[sub_df_.duplicated(keep='first', subset=['topic_name']), 'topic_name'] + '_' \
            + str(sub_df_.loc[sub_df_.duplicated(keep='first', subset=['topic_name']), 'callback_object']) 
            
        # sub_df_ = sub_df[sub_df['name'] == node.name]
        assert ApplicationFactory._get_duplicate_num_max(sub_df_['topic_name'].values) <= 1, \
            '{} node has same topic_name'.format(node.name)

        for i, (_, df) in enumerate(sub_df_.iterrows()):
            if df['topic_name'] in ['/parameter_events']:
                continue
            callback = SubscribeCallback(node=node,
                topic_name=df['topic_name'], symbol=df['symbol'])
            node.callbacks.append(callback)

        pub_df_ = pub_df[pub_df['name'] == node.name]
        for _, df in pub_df_.iterrows():
            if df['topic_name'] in ['/rosout', '/parameter_events']:
                continue
            if len(node.callbacks) == 1:
                node.pubs.append(
                    Publish(topic_name=df['topic_name'], callback=node.callbacks[0]))
            else:
                node.pubs.append(
                    Publish(topic_name=df['topic_name'], callback=None))
    return node

def create_app(cls, data_util):
    if True:
        app = Application()
        for _, node_info in data_util.data.nodes.drop('timestamp', axis=1).iterrows():
            node = create_node(node_info, data_util)
            app.nodes.append(node)
        return app

app = create_app(None, data_util)
app.import_trace(trace_path)


/home/usrg/.local/lib/python3.8/site-packages/pandas/core/indexing.py:1773: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(ilocs[0], value, pi)


found converted file: /home/usrg/.ros/tracing/session-20220527110659/converted
 [100%] [Ros2Handler]
warn: callback 36010656 is not registered. your application may contain rclpy app.


AssertionError: Failed to get publish record

In [9]:
def format_title(symbol: str, owner_info: tuple) -> str:
    if owner_info:
        owner_type = owner_info[0]

        title = owner_type + ': '
        if owner_type == 'Timer':
            sym = symbol.split('(')[0]
            if '::' in sym:
                sym = sym.split('::')[-1]
            title += owner_info[1]['period'] + ' ' + sym
        elif owner_type == 'Subscription':
            title += owner_info[1]['node'] + ' ' + owner_info[1]['topic']
        elif owner_type == 'Publisher':
            title += owner_info[1]['node'] + ' ' + owner_info[1]['topic']
    else:
        title = symbol if len(symbol) <= 60 else symbol[:60]

    return title

def format_filename(symbol: str, owner_info: tuple) -> str:
    owner_type = owner_info[0]
    
    title = owner_type.lower() + '_'
    if owner_type == 'Timer':
        sym = symbol.split('(')[0]
        if '::' in sym:
            sym = sym.split('::')[-1]
        title += owner_info[1]['period'] + '_' + sym
    elif owner_type == 'Subscription':
        title += owner_info[1]['node'] + '_' + owner_info[1]['topic'].replace('/', '.')
    elif owner_type == 'Publisher':
        title += owner_info[1]['node'] + '_' + owner_info[1]['topic'].replace('/', '.')

    # if isinstance(owner_info, tuple):
    #     title = sym + '::' + str(owner_info) 
    # elif isinstance(owner_info,str):
    #     title = owner_info
    # else:
    #     title = sym

    return title

In [30]:
# Plot durations separately
from bokeh.io import export_png
colour_i = 0
export_path='./export/latency/'

for obj, symbol in callback_symbols.items():
    owner_info = data_util.get_callback_owner_info(obj)
    if owner_info is None:
        owner_info = '[unknown]'

    title = format_title(symbol, owner_info)

    # Duration
    duration_df = data_util.get_callback_durations(obj)
    starttime = duration_df.loc[:, 'timestamp'].iloc[0].strftime('%Y-%m-%d %H:%M')
    source = ColumnDataSource(duration_df)
    duration = figure(
        title=title,
        x_axis_label=f'start ({starttime})',
        y_axis_label='duration (ms)',
        plot_width=psize, plot_height=psize,
    )
    duration.title.align = 'center'
    duration.line(
        x='timestamp',
        y='duration',
        legend=str(symbol),
        line_width=2,
        source=source,
        line_color=colours[colour_i],
    )
    duration.legend.label_text_font_size = '11px'
    duration.xaxis[0].formatter = DatetimeTickFormatter(seconds=['%Ss'])

    # Histogram
    dur_hist, edges = np.histogram(duration_df['duration'])
    duration_hist = pd.DataFrame({
        'duration': dur_hist, 
        'left': edges[:-1], 
        'right': edges[1:],
    })
    hist = figure(
        title='Duration histogram',
        x_axis_label='duration (ms)',
        y_axis_label='frequency',
        plot_width=psize, plot_height=psize,
    )
    hist.title.align = 'center'
    hist.quad(
        bottom=0,
        top=duration_hist['duration'], 
        left=duration_hist['left'],
        right=duration_hist['right'],
        fill_color=colours[colour_i],
        line_color=colours[colour_i],
    )

    # colour_i += 1 ## Intentional overflow, remove
    # show(row(duration, hist))
    # export_png(duration, filename=export_path + format_filename(symbol, owner_info) + '_duration.png')
    # export_png(hist, filename=export_path + format_filename(symbol, owner_info) + '_hist.png')

In [12]:
# Plot durations in one plot
earliest_date = None
for obj, symbol in callback_symbols.items():
    duration_df = data_util.get_callback_durations(obj)
    thedate = duration_df.loc[:, 'timestamp'].iloc[0]
    if earliest_date is None or thedate <= earliest_date:
        earliest_date = thedate

TOOLTIPS = [
    ("Callback", "$name"),
    ("(x, y)", "($x, $y)"),
]

starttime = earliest_date.strftime('%Y-%m-%d %H:%M')
duration = figure(
    title='Callback durations',
    x_axis_label=f'start ({starttime})',
    y_axis_label='duration (ms)',
    plot_width=psize*2, plot_height=psize,
    tooltips=TOOLTIPS
)

colour_i = 0
for obj, symbol in callback_symbols.items():
    owner_info = data_util.get_callback_owner_info(obj)
    duration_df = data_util.get_callback_durations(obj)
    source = ColumnDataSource(duration_df)
    duration.title.align = 'center'
    duration.line(
        x='timestamp',
        y='duration',
        legend=format_title(symbol, owner_info),
        name=format_title(symbol, owner_info),
        line_width=2,
        source=source,
        line_color=colours[colour_i%3],
    )
    colour_i += 1
    duration.legend.label_text_font_size = '11px'
    duration.xaxis[0].formatter = DatetimeTickFormatter(seconds=['%Ss'])

show(duration)